In [435]:
import os, time
from py_clob_client.constants import POLYGON
from py_clob_client.client import ClobClient
from py_clob_client.clob_types import OrderArgs, ApiCreds, BalanceAllowanceParams, AssetType
from dotenv import load_dotenv

load_dotenv()

host = "https://clob.polymarket.com"
key = os.getenv("PRIVATE_KEY")
chain_id = POLYGON

client = ClobClient(host, key=key, chain_id=chain_id)
client.set_api_creds(client.create_or_derive_api_creds())

In [436]:
biden_drops_out = [{'token_id': '80466862227762400456474037114326989569691448086113369690204721936360568404468', 'outcome': 'Yes', 'price': 0.515, 'winner': False}, {'token_id': '55053017623018167103206225381535351479731721326578895660347356086269854794785', 'outcome': 'No', 'price': 0.485, 'winner': False}]
biden_nominee = [{'token_id': '29771515314065403331935508893946579645282141892225585852084723308418208825505', 'outcome': 'Yes', 'price': 0.625, 'winner': False}, {'token_id': '73890423855099261268197674979498041824881965319673879879507212961483126998683', 'outcome': 'No', 'price': 0.375, 'winner': False}]

In [380]:
next_cursor = ""
while True:
    print(f"fetching {next_cursor} ...")
    markets = client.get_markets(next_cursor=next_cursor)
    for market in markets['data']:
        if ('Biden' in market['question']) and ('democrats.org' in market['description']):
            print(market)
    next_cursor = markets['next_cursor']
    time.sleep(1)
    # break

fetching  ...
{'enable_order_book': True, 'active': True, 'closed': False, 'archived': False, 'accepting_orders': True, 'accepting_order_timestamp': None, 'minimum_order_size': 5, 'minimum_tick_size': 0.01, 'condition_id': '0xf5875410202b3545491774ab5e712a6e05a0ffe780c52270cc8d70cc95164411', 'question_id': '0x06a4bcc28c8b76961ed6caa7de6e103d3b4cc8a539ebb376fc970928199e5c18', 'question': '[Single Market] Will Joe Biden win the U.S. 2024 Democratic presidential nomination?', 'description': 'This market will resolve to “Yes” if Joe Biden wins the 2024 nomination of the Democratic Party for U.S. president. Otherwise, this market will resolve to “No”.\n\nThe resolution source for this market will be a consensus of official Democratic Party sources, including https://democrats.org/.\n\nAny replacement of the nominee before election day will not change the resolution of the market.', 'market_slug': 'will-joe-biden-win-the-us-2024-democratic-presidential-nomination', 'end_date_iso': '2024-08-1

KeyboardInterrupt: 

In [437]:
from importlib import reload
import polymarket_classes
reload(polymarket_classes)
from polymarket_classes import LinearPiecewiseFunction, Book, Market, calculate_arbitrage

def get_book_for_token_id(token_id: str) -> Book:
    orderbook = client.get_order_book(token_id)
    return Book(
        bids=[(float(os.price), float(os.size)) for os in orderbook.bids],
        asks=[(float(os.price), float(os.size)) for os in orderbook.asks],
    )

In [438]:
biden_drops_out_yes = get_book_for_token_id(biden_drops_out[0]['token_id'])
biden_nominee_no = get_book_for_token_id(biden_nominee[1]['token_id'])

In [439]:
biden_drops_out_yes.print_book()
biden_nominee_no.print_book()

Order Book
--------------------------------------------------------------------------------
                 Bids                   |                  Asks                  
   Price        Size       Value ($)    |    Price        Size       Value ($)   
--------------------------------------------------------------------------------
0.46        1042.07      479.35         | 0.48        1400.00      672.00        
0.45        2597.15      1168.72        | 0.49        3780.98      1852.68       
0.44        188.00       82.72          | 0.50        11827.17     5913.59       
0.43        3017.00      1297.31        | 0.51        698.14       356.05        
0.42        250.00       105.00         | 0.52        2700.00      1404.00       
--------------------------------------------------------------------------------
Order Book
--------------------------------------------------------------------------------
                 Bids                   |                  Asks                 

In [440]:
calculate_arbitrage(biden_drops_out_yes, biden_nominee_no)

2024-07-14 02:53:40.754249,None,(7094.219999999999, 0.42),(7094.219999999999, 0.39),None


In [442]:
import pickle

with open("books/80466862227762400456474037114326989569691448086113369690204721936360568404468_20240714-03071720926476.pkl", "rb") as f:
    book = pickle.load(f)

In [444]:
book.asks

[(0.48, 1370.0),
 (0.49, 3789.07),
 (0.5, 11819.08),
 (0.51, 698.14),
 (0.52, 2700.0),
 (0.54, 200.0),
 (0.57, 1000.0),
 (0.59, 1859.66),
 (0.6, 3899.0),
 (0.61, 432.0),
 (0.62, 200.0),
 (0.63, 1477.55),
 (0.64, 200.0),
 (0.65, 1087.7),
 (0.66, 4248.04),
 (0.67, 1275.74),
 (0.68, 1000.0),
 (0.69, 1055.15),
 (0.7, 500.0),
 (0.72, 100.0),
 (0.73, 522.0),
 (0.74, 13500.0),
 (0.75, 979.63),
 (0.77, 4769.95),
 (0.79, 6975.63),
 (0.8, 258538.43),
 (0.82, 20009.0),
 (0.84, 400.0),
 (0.85, 1157.8),
 (0.87, 1846.0),
 (0.88, 500.0),
 (0.89, 1036.0),
 (0.9, 20050.25),
 (0.91, 5.0),
 (0.92, 2874.5),
 (0.93, 13.54),
 (0.94, 1250.0),
 (0.95, 30095.36),
 (0.96, 2000.0),
 (0.97, 8.0),
 (0.99, 5373.36)]